In [2]:
!pip install PyAthena

In [3]:
!pip install --upgrade gensim

In [4]:
from __future__ import print_function
import numpy as np
import string
import nltk
from nltk import word_tokenize
import datetime
import pandas as pd
import matplotlib.pyplot as plt
import os
import boto3
from botocore.client import ClientError
# below is used to print out pretty pandas dataframes
from IPython.display import display, HTML

from pyathena import connect
from pyathena.pandas.util import as_pandas
import torch
import torch.nn as nn
import time
nltk.download('punkt')

[nltk_data] Downloading package punkt to /home/ec2-user/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [5]:
s3 = boto3.resource('s3')
client = boto3.client("sts")
account_id = client.get_caller_identity()["Account"]
my_session = boto3.session.Session()
region = my_session.region_name
athena_query_results_bucket = 'aws-athena-query-results-'+account_id+'-'+region

try:
    s3.meta.client.head_bucket(Bucket=athena_query_results_bucket)
except ClientError:
    bucket = s3.create_bucket(Bucket=athena_query_results_bucket)
    print('Creating bucket '+athena_query_results_bucket)
cursor = connect(s3_staging_dir='s3://'+athena_query_results_bucket+'/athena/temp').cursor()

fetch the notes from the default database from diabetic_patient_notes_agg table

In [6]:
query = 'select * from default.diabetic_patients_notes_agg'
cursor.execute(query)
cohort_patients_df = as_pandas(cursor)

In [7]:
cohort_patients_df.head()

subject_id  chart_date                                          notes_agg
0       18673  2132-08-24  Admission Date:  [**2132-8-15**]              ...
1       18673  2132-09-03  Sinus rhythm.  Non-specific inferior and anter...
2       18673  2132-09-04  Possible ectopic atrial rhythm with ventricula...
3       24743  2134-08-09  [**2134-8-9**] 5:41 PM\n CHEST PORT. LINE PLAC...
4       24743  2134-08-11  [**2134-8-11**] 8:40 AM\n PORTABLE ABDOMEN    ...

In [17]:
import time
#import numpy as np
import string
#from nltk import word_tokenize
import re


#input
# df: a dataframe returned by `load_dataset`
#output
# clinical_notes: a list of clinical notes where each clinical note is broke into a list of words 
def preprocess_dataset(df):    
    ''' Preprocess the text data. And return a list of clinical notes. '''
    clinical_notes = []
    
    df.notes_agg = df.notes_agg.fillna(' ')  # remove NA
    df.notes_agg = df.notes_agg.str.replace('\n',' ')  # remove newline
    df.notes_agg = df.notes_agg.str.replace('\r',' ')
    
    
    #remove punctuation 
    df.notes_agg = [re.sub(r'[^\w\s]','',x) for x in df.notes_agg.tolist()]
    df.notes_agg = [re.sub('['+string.punctuation+']','',x) for x in df.notes_agg.tolist()]
    
    #remove numbers
    df.notes_agg = [re.sub("\d+",'',x) for x in df.notes_agg.tolist()]
    
    df.notes_agg = df.notes_agg.str.lower()  # convert to lower case
    
    # tokenize
    for note in df.notes_agg.values:
        note_tokenized = word_tokenize(note)
        clinical_notes.append(note_tokenized)

    return clinical_notes

In [ ]:
clinical_notes = preprocess_dataset(cohort_patients_notes_df)

In [8]:
ids = np.unique(cohort_patients_df.subject_id)

In [15]:
ids[0]

13

In [27]:
from gensim.models import Word2Vec
#preprocess and train the first patient notes with subject_id 13
clinical_notes = preprocess_dataset(cohort_patients_df.loc[cohort_patients_df.subject_id==13])
notes_model = Word2Vec(clinical_notes, vector_size=200, min_count=10, workers=4)

for idx in range(1,len(ids)):
    df = cohort_patients_df.loc[cohort_patients_df.subject_id==ids[idx]]
    addition_notes = preprocess_dataset(df)
    notes_model.build_vocab(addition_notes, update=True)
    notes_model.train(addition_notes, total_examples=notes_model.corpus_count, epochs=notes_model.epochs)
    

/home/ec2-user/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/pandas/core/generic.py:5170: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[name] = value
/home/ec2-user/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/pandas/core/generic.py:5170: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[name] = value
/home/ec2-user/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/pandas/core/generic.py:5170: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a Data

/home/ec2-user/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/pandas/core/generic.py:5170: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[name] = value
/home/ec2-user/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/pandas/core/generic.py:5170: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[name] = value
/home/ec2-user/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/pandas/core/generic.py:5170: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a Data

/home/ec2-user/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/pandas/core/generic.py:5170: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[name] = value
/home/ec2-user/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/pandas/core/generic.py:5170: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[name] = value
/home/ec2-user/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/pandas/core/generic.py:5170: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a Data

/home/ec2-user/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/pandas/core/generic.py:5170: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[name] = value
/home/ec2-user/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/pandas/core/generic.py:5170: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[name] = value
/home/ec2-user/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/pandas/core/generic.py:5170: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a Data

/home/ec2-user/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/pandas/core/generic.py:5170: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[name] = value
/home/ec2-user/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/pandas/core/generic.py:5170: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[name] = value
/home/ec2-user/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/pandas/core/generic.py:5170: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a Data

...

/home/ec2-user/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/pandas/core/generic.py:5170: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[name] = value
/home/ec2-user/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/pandas/core/generic.py:5170: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[name] = value
/home/ec2-user/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/pandas/core/generic.py:5170: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a Data

/home/ec2-user/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/pandas/core/generic.py:5170: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[name] = value
/home/ec2-user/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/pandas/core/generic.py:5170: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[name] = value
/home/ec2-user/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/pandas/core/generic.py:5170: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a Data

/home/ec2-user/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/pandas/core/generic.py:5170: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[name] = value
/home/ec2-user/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/pandas/core/generic.py:5170: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[name] = value
/home/ec2-user/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/pandas/core/generic.py:5170: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a Data

/home/ec2-user/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/pandas/core/generic.py:5170: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[name] = value
/home/ec2-user/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/pandas/core/generic.py:5170: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[name] = value
/home/ec2-user/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/pandas/core/generic.py:5170: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a Data

/home/ec2-user/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/pandas/core/generic.py:5170: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[name] = value
/home/ec2-user/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/pandas/core/generic.py:5170: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[name] = value
/home/ec2-user/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/pandas/core/generic.py:5170: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a Data

In [26]:
cohort_patients_df.loc[cohort_patients_df.subject_id==13]

subject_id  chart_date  \
42773          13  2167-01-09   
42774          13  2167-01-10   
42775          13  2167-01-11   
42776          13  2167-01-12   

                                               notes_agg  
42773  Sinus rhythm/ Non-diagnostic inferior and late...  
42774  [**2167-1-10**] A:\n\nNeuro: alert and oriente...  
42775  Pt. alert when awakened. Sleeping in long naps...  
42776  Pt. had a comfortable night. Medicated prn wit...

In [32]:
#retrieve the keyed vectors
note_vectors = notes_model.wv

In [33]:
#save the keyed vectors
note_vectors.save('note_vectors.kv')

In [34]:
len(note_vectors)

25555

In [35]:
note_vectors.most_similar("admission")

[('arrival', 0.48404988646507263),
 ('hospitalization', 0.4680754840373993),
 ('presentation', 0.4402068853378296),
 ('adm', 0.43097272515296936),
 ('arriving', 0.4064110815525055),
 ('study', 0.40081021189689636),
 ('examinations', 0.3619668185710907),
 ('transfer', 0.3500061333179474),
 ('stay', 0.3469494879245758),
 ('admit', 0.3455927073955536)]

In [23]:
#04/15/2021
query = 'select * from default.diabetic_patients_cohort'
cursor.execute(query)
cohort_patients_df = as_pandas(cursor)

In [24]:
cohort_patients_df.head()

subject_id          admit_time      discharge_time  mortality_flag
0        1454 2108-01-04 08:00:00 2108-01-08 13:49:00               0
1        1337 2137-03-25 12:26:00 2137-04-03 11:55:00               0
2        2511 2191-10-12 21:55:00 2191-10-26 17:57:00               1
3        3435 2148-04-27 21:03:00 2148-05-02 14:55:00               0
4        3868 2125-05-03 17:03:00 2125-11-05 16:02:00               1

In [25]:
#check number of patients in each class
class_0 = cohort_patients_df[cohort_patients_df.mortality_flag==0]
class_1 = cohort_patients_df[cohort_patients_df.mortality_flag==1]

print('class 0: ',class_0.shape)
print('class 1: ',class_1.shape)

class 0:  (8605, 4)
class 1:  (1217, 4)


In [8]:
! pip install imbalanced-learn

     |████████████████████████████████| 206 kB 27.9 MB/s eta 0:00:01


In [26]:
from sklearn.utils import resample
## Upsampling to balance dataset
#separate class into majority and minority classes
df_majority = cohort_patients_df[cohort_patients_df.mortality_flag==0]
df_minority = cohort_patients_df[cohort_patients_df.mortality_flag==1]

#upsample the minority class
df_minority_upsampled = resample(df_minority, replace=True, n_samples=class_0.shape[0],
                                random_state=123)

#comibine majority dataframe with new minority dataframe
df_upsampled = pd.concat([df_majority,df_minority_upsampled])

#display new class counts
df_upsampled.mortality_flag.value_counts()


1    8605
0    8605
Name: mortality_flag, dtype: int64

In [17]:
df_upsampled.shape

(17210, 4)

In [19]:
print(df_upsampled[df_upsampled.mortality_flag==1].shape)
print(df_upsampled[df_upsampled.mortality_flag==0].shape)

(8605, 4)
(8605, 4)


In [21]:
#save new dataframe
compression_opts = dict(method='zip',archive_name='balanced_chohort.csv')
df_upsampled.to_csv('balanced_chohort.csv', index=False, compression=compression_opts)

In [15]:
#save df to s3
df_upsampled.to_csv('s3://'+athena_query_results_bucket+'/athena/temp/csv/balanced_cohort.csv', index=False)

In [12]:
df_upsampled.dtypes

subject_id                 int64
admit_time        datetime64[ns]
discharge_time    datetime64[ns]
mortality_flag             int64
dtype: object

In [13]:
athena_query_results_bucket

'aws-athena-query-results-067114122515-us-east-1'

## 04/16/2021

In [27]:
from sklearn.model_selection import train_test_split

train_cohort_df, test_cohort_df = train_test_split(cohort_patients_df, train_size=0.8,
                                                 random_state=230729, shuffle=True)

In [28]:
print(train_cohort_df.shape)
print(test_cohort_df.shape)

(7857, 4)
(1965, 4)


In [29]:
#test_cohort_df.head(20)
#check number of patients in each class
class_0 = train_cohort_df[train_cohort_df.mortality_flag==0]
class_1 = train_cohort_df[train_cohort_df.mortality_flag==1]

print(class_0.shape)
print(class_1.shape)

(6895, 4)
(962, 4)


In [30]:
#Upsample the training data
from sklearn.utils import resample
## Upsampling to balance dataset
#separate class into majority and minority classes
df_majority = train_cohort_df[train_cohort_df.mortality_flag==0]
df_minority = train_cohort_df[train_cohort_df.mortality_flag==1]

#upsample the minority class
df_minority_upsampled = resample(df_minority, replace=True, n_samples=class_0.shape[0],
                                random_state=230729)

#comibine majority dataframe with new minority dataframe
df_upsampled = pd.concat([df_majority,df_minority_upsampled])

#display new class counts
df_upsampled.mortality_flag.value_counts()

1    6895
0    6895
Name: mortality_flag, dtype: int64

In [18]:
#save df to s3
df_upsampled.to_csv('s3://'+athena_query_results_bucket+'/athena/temp/train/train_cohort.csv', index=False)

In [19]:
#save test cohort to bucket
test_cohort_df.to_csv('s3://'+athena_query_results_bucket+'/athena/temp/test/test_cohort.csv', index=False)

## 04/18/2021

In [31]:
df_upsampled.shape

(13790, 4)

In [32]:
df_upsampled.reset_index(inplace=True)

In [33]:
df_upsampled.tail(20)

index  subject_id          admit_time      discharge_time  \
13770   7351         914 2177-12-16 22:45:00 2178-06-04 21:17:00   
13771   6001        6464 2151-09-30 15:04:00 2152-04-09 18:52:00   
13772   4319       12403 2184-01-30 09:00:00 2185-04-17 19:50:00   
13773   3349       16608 2148-05-24 00:53:00 2148-06-08 01:55:00   
13774   5727       42525 2125-02-01 18:40:00 2125-04-15 06:48:00   
13775   5866       14990 2146-09-28 14:44:00 2148-12-25 09:52:00   
13776   3325       94589 2127-02-10 01:21:00 2127-02-14 23:30:00   
13777   8534       29690 2196-02-11 11:01:00 2203-11-10 12:30:00   
13778   4639        5555 2189-08-05 02:41:00 2190-08-07 21:22:00   
13779   2147       40428 2170-06-16 19:35:00 2170-06-22 19:10:00   
13780   8989       95968 2195-04-28 21:25:00 2195-05-03 13:00:00   
13781   2904       63030 2139-10-25 18:22:00 2139-10-28 05:50:00   
13782   4867       29163 2139-07-17 07:15:00 2139-09-24 21:32:00   
13783   5793       18200 2114-03-12 09:27:00 2121-06-05 21:35:00   
13784   8186       18252 2137-09-25 00:04:00 2137-10-09 19:30:00   
13785   8701       44059 2127-07-24 18:47:00 2127-08-07 21:15:00   
13786   1889       26039 2152-03-17 05:40:00 2152-03-23 10:30:00   
13787   9225       44373 2187-05-14 20:07:00 2187-06-06 12:00:00   
13788   5947       23990 2132-07-17 17:00:00 2133-08-26 18:39:00   
13789   5159       81449 2155-07-25 06:52:00 2155-08-02 14:20:00   

       mortality_flag  
13770               1  
13771               1  
13772               1  
13773               1  
13774               1  
13775               1  
13776               1  
13777               1  
13778               1  
13779               1  
13780               1  
13781               1  
13782               1  
13783               1  
13784               1  
13785               1  
13786               1  
13787               1  
13788               1  
13789               1

In [36]:
df_upsampled[df_upsampled['index']==7351]

index  subject_id          admit_time      discharge_time  \
7851    7351         914 2177-12-16 22:45:00 2178-06-04 21:17:00   
8121    7351         914 2177-12-16 22:45:00 2178-06-04 21:17:00   
8363    7351         914 2177-12-16 22:45:00 2178-06-04 21:17:00   
9639    7351         914 2177-12-16 22:45:00 2178-06-04 21:17:00   
10916   7351         914 2177-12-16 22:45:00 2178-06-04 21:17:00   
11160   7351         914 2177-12-16 22:45:00 2178-06-04 21:17:00   
12884   7351         914 2177-12-16 22:45:00 2178-06-04 21:17:00   
13770   7351         914 2177-12-16 22:45:00 2178-06-04 21:17:00   

       mortality_flag  
7851                1  
8121                1  
8363                1  
9639                1  
10916               1  
11160               1  
12884               1  
13770               1

In [37]:
df_upsampled.reset_index(inplace=True)

In [38]:
df_upsampled.head()

level_0  index  subject_id          admit_time      discharge_time  \
0        0   9600        7177 2101-04-18 18:29:00 2101-04-26 16:50:00   
1        1   1728       74144 2187-03-05 21:28:00 2193-10-17 14:00:00   
2        2   7320       54353 2135-01-24 21:05:00 2136-08-23 16:50:00   
3        3   5399       82000 2131-09-05 23:53:00 2131-09-17 16:50:00   
4        4    119       26161 2107-01-11 07:30:00 2113-07-20 17:00:00   

   mortality_flag  
0               0  
1               0  
2               0  
3               0  
4               0

In [39]:
df_upsampled[df_upsampled['index']==7351]

level_0  index  subject_id          admit_time      discharge_time  \
7851      7851   7351         914 2177-12-16 22:45:00 2178-06-04 21:17:00   
8121      8121   7351         914 2177-12-16 22:45:00 2178-06-04 21:17:00   
8363      8363   7351         914 2177-12-16 22:45:00 2178-06-04 21:17:00   
9639      9639   7351         914 2177-12-16 22:45:00 2178-06-04 21:17:00   
10916    10916   7351         914 2177-12-16 22:45:00 2178-06-04 21:17:00   
11160    11160   7351         914 2177-12-16 22:45:00 2178-06-04 21:17:00   
12884    12884   7351         914 2177-12-16 22:45:00 2178-06-04 21:17:00   
13770    13770   7351         914 2177-12-16 22:45:00 2178-06-04 21:17:00   

       mortality_flag  
7851                1  
8121                1  
8363                1  
9639                1  
10916               1  
11160               1  
12884               1  
13770               1

In [52]:
df_upsampled[df_upsampled['subject_id']==81449]

new_subject_id  subject_id          admit_time      discharge_time  \
6895             6895       81449 2155-07-25 06:52:00 2155-08-02 14:20:00   
7152             7152       81449 2155-07-25 06:52:00 2155-08-02 14:20:00   
10398           10398       81449 2155-07-25 06:52:00 2155-08-02 14:20:00   
12226           12226       81449 2155-07-25 06:52:00 2155-08-02 14:20:00   
13789           13789       81449 2155-07-25 06:52:00 2155-08-02 14:20:00   

       mortality_flag  
6895                1  
7152                1  
10398               1  
12226               1  
13789               1

In [42]:
df_upsampled.shape

(13790, 6)

In [43]:
len(np.unique(df_upsampled.level_0))

13790

In [47]:
df_upsampled = df_upsampled.drop(columns=['index'])

In [51]:
df_upsampled = df_upsampled.rename(columns={"level_0":"new_subject_id"})

In [53]:
#save new df to s3
df_upsampled.to_csv('s3://'+athena_query_results_bucket+'/athena/temp/train2/train_cohort.csv', index=False)